In [1]:
!pip install --upgrade pip setuptools wheel
!pip install numpy
!pip install mindspore
!pip install jieba
!pip install scikit-learn
!pip install joblib
!pip install pandas
!pip install gensim

Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://mirrors.huaweicloud.com/repository/pypi/simple
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 18.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 23.7 MB/s eta 0:00:00
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
openmind 0.9.1 requires datasets<=2.21.0,>=2.18.0, but you have datasets 3.2.0 which is incompatible.
openmind 0.9.1 requires openmind-hub==0.9.0, but you have openmind-hub 0.9.1 which is incompatible.
openmind 0.9.1 requires setuptools==69.5.1, but you have setuptools 78.1.0 which

In [1]:
import jieba
import numpy as np
import pandas as pd
import subprocess
import mindspore as ms
from mindspore import Tensor, nn, ops
from mindspore.dataset import GeneratorDataset
from gensim.models.word2vec import Word2Vec
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
import joblib

/home/service/.local/lib/python3.10/site-packages/numpy/core/getlimits.py:518: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/home/service/.local/lib/python3.10/site-packages/numpy/core/getlimits.py:89: UserWarning: The value of the smallest subnormal for <class 'numpy.float64'> type is zero.
  return self._float_to_str(self.smallest_subnormal)
/home/service/.local/lib/python3.10/site-packages/numpy/core/getlimits.py:518: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  setattr(self, word, getattr(machar, word).flat[0])
/home/service/.local/lib/python3.10/site-packages/numpy/core/getlimits.py:89: UserWarning: The value of the smallest subnormal for <class 'numpy.float32'> type is zero.
  return self._float_to_str(self.smallest_subnormal)


In [3]:
command = ["git", "clone", "https://source-xihe.mindspore.cn/makercxj/NewsTitle_classify.git"]
# 执行命令
try:
    subprocess.run(command, check=True)
    print("文件下载成功！")
except subprocess.CalledProcessError as e:
    print(f"下载失败: {e}")

Cloning into 'NewsTitle_classify'...


文件下载成功！


In [4]:
pos = pd.read_csv('NewsTitle_classify/culture_title.txt', encoding='UTF-8', header=None)
neg = pd.read_csv('NewsTitle_classify/nature_title.txt', encoding='UTF-8',header=None)

In [5]:
pos['words'] = pos[0].apply(lambda x: jieba.lcut(x))
neg['words'] = neg[0].apply(lambda x: jieba.lcut(x))

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 1.358 seconds.
Prefix dict has been built successfully.


In [6]:
x = np.concatenate((pos['words'], neg['words']))
y = np.concatenate((np.ones(len(pos)), np.zeros(len(neg))))

In [7]:
word2vec = Word2Vec(x, vector_size=300, window=3, min_count=5, sg=1, hs=1,epochs=10, workers=25)
word2vec.save('word2vec.model')

In [8]:
def total_vector(words):
    vec = np.zeros(300)
    for word in words:
        try:
            vec += word2vec.wv[word]
        except KeyError:
            continue
    return vec

In [9]:
train_vec = np.array([total_vector(words) for words in x])

In [10]:
X_train, X_test, y_train, y_test = train_test_split(train_vec, y,test_size=0.2, random_state=42)

In [11]:
X_train_ms = Tensor(X_train, dtype=ms.float32)
y_train_ms = Tensor(y_train, dtype=ms.float32)
X_test_ms = Tensor(X_test, dtype=ms.float32)
y_test_ms = Tensor(y_test, dtype=ms.float32)

In [12]:
class SVM(nn.Cell):
    def __init__(self, input_size):
        super(SVM, self).__init__()
        self.linear = nn.Dense(input_size, 1)
    def construct(self, x):
        return self.linear(x)

In [13]:
model = SVM(300)
loss_fn = nn.BCEWithLogitsLoss()
optimizer = nn.Adam(model.trainable_params(), learning_rate=0.001)

In [14]:
net_with_loss = nn.WithLossCell(model, loss_fn)
train_net = nn.TrainOneStepCell(net_with_loss, optimizer)

In [33]:
def train_loop(train_net, dataset):
    model.set_train()
    for epoch in range(50):
        for data, label in dataset:
            label = label.view(-1, 1)
            loss = train_net(data, label)
        if epoch % 5 == 0:
            print(f"Epoch {epoch}, Loss: {loss.asnumpy()}")

In [25]:
dataset = GeneratorDataset(list(zip(X_train_ms, y_train_ms)), ['data','label'])
dataset = dataset.batch(32)

In [36]:
try:
    train_loop(train_net, dataset)
except Exception as e:
    print(f"Exception: {e}")

Epoch 0, Loss: 0.07082682847976685
Epoch 5, Loss: 0.01766294613480568
Epoch 10, Loss: 0.030258089303970337
Epoch 15, Loss: 0.028694897890090942
Epoch 20, Loss: 0.0006060741143301129
Epoch 25, Loss: 0.01854262501001358
Epoch 30, Loss: 0.0689435601234436
Epoch 35, Loss: 0.2601395547389984
Epoch 40, Loss: 0.06100676208734512
Epoch 45, Loss: 0.040831662714481354


In [37]:
model.set_train(False)
y_pred = (model(X_test_ms).asnumpy() > 0.5).astype(int)
print(f"模型准确率: {accuracy_score(y_test, y_pred):.4f}")
print(classification_report(y_test, y_pred, target_names=['生态环境类', '文化体育类']))

模型准确率: 0.9754
              precision    recall  f1-score   support

       生态环境类       0.96      1.00      0.98       116
       文化体育类       1.00      0.94      0.97        87

    accuracy                           0.98       203
   macro avg       0.98      0.97      0.97       203
weighted avg       0.98      0.98      0.98       203



In [38]:
def svm_predict(query):
    words = jieba.lcut(query)
    vec = total_vector(words)
    vec_ms = Tensor(vec.reshape(1, -1), dtype=ms.float32)
    result = (model(vec_ms).asnumpy() > 0.5).astype(int)
    proba = ops.Sigmoid()(model(vec_ms)).asnumpy()[0][0]
    if int(result) == 1:
        print(f'类别：文化体育类 (概率: {proba:.4f})')
    else:
        print(f'类别：生态环境类 (概率: {1 - proba:.4f})')

In [39]:
svm_predict('文化体育融合新发展，全民共享健康生活')
svm_predict('生态修复与保护加速推进，绿色发展绘就美丽未来')

类别：文化体育类 (概率: 0.8426)
类别：生态环境类 (概率: 0.9994)
